<h3> Project Step 1: Task Selection and Data Cleaning </h3>

In [1]:
import pandas as pd
from scipy import sparse
from scipy.sparse import csr_matrix

In [2]:
data = r"C:\Users\akile\Downloads\Book Dataset\Ratings.csv"
df = pd.read_csv(data, delimiter=';')
df.head()

User-ID        ISBN  Rating
0   276725  034545104X       0
1   276726  0155061224       5
2   276727  0446520802       0
3   276729  052165615X       3
4   276729  0521795028       6

In [3]:
df.drop_duplicates()

User-ID         ISBN  Rating
0         276725   034545104X       0
1         276726   0155061224       5
2         276727   0446520802       0
3         276729   052165615X       3
4         276729   0521795028       6
...          ...          ...     ...
1149775   276704   1563526298       9
1149776   276706   0679447156       0
1149777   276709   0515107662      10
1149778   276721   0590442449      10
1149779   276723  05162443314       8

[1149780 rows x 3 columns]

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1149780 entries, 0 to 1149779
Data columns (total 3 columns):
 #   Column   Non-Null Count    Dtype 
---  ------   --------------    ----- 
 0   User-ID  1149780 non-null  int64 
 1   ISBN     1149780 non-null  object
 2   Rating   1149780 non-null  int64 
dtypes: int64(2), object(1)
memory usage: 26.3+ MB


In [5]:
user_to_idx = {user: idx for idx, user in enumerate(df['User-ID'].unique())}
idx_to_user = {idx: user for user, idx in user_to_idx.items()}
print(len(df["User-ID"].unique()))

105283


In [6]:
user_to_idx

{276725: 0,
 276726: 1,
 276727: 2,
 276729: 3,
 276733: 4,
 276736: 5,
 276737: 6,
 276744: 7,
 276745: 8,
 276746: 9,
 276747: 10,
 276748: 11,
 276751: 12,
 276754: 13,
 276755: 14,
 276760: 15,
 276762: 16,
 276765: 17,
 276768: 18,
 276772: 19,
 276774: 20,
 276780: 21,
 276786: 22,
 276788: 23,
 276796: 24,
 276798: 25,
 276800: 26,
 276803: 27,
 276804: 28,
 276806: 29,
 276808: 30,
 276811: 31,
 276812: 32,
 276813: 33,
 276814: 34,
 276817: 35,
 276820: 36,
 276822: 37,
 276827: 38,
 276828: 39,
 276830: 40,
 276832: 41,
 276833: 42,
 276835: 43,
 276837: 44,
 276838: 45,
 276840: 46,
 276842: 47,
 276847: 48,
 276848: 49,
 276850: 50,
 276852: 51,
 276853: 52,
 276854: 53,
 276856: 54,
 276857: 55,
 276859: 56,
 276861: 57,
 276862: 58,
 276863: 59,
 276866: 60,
 276869: 61,
 276870: 62,
 276872: 63,
 276873: 64,
 276875: 65,
 276878: 66,
 276879: 67,
 276884: 68,
 276887: 69,
 276888: 70,
 276889: 71,
 276890: 72,
 276896: 73,
 276904: 74,
 276905: 75,
 276911: 76,
 276912: 

In [7]:
isbn_to_idx = {isbn: idx for idx, isbn in enumerate(df['ISBN'].unique())}
user_to_idx = {user: idx for idx, user in enumerate(df['User-ID'].unique())}

# Convert the IDs to integer indices
book_sparse_matrix = sparse.csr_matrix(
    (
        df.Rating.values,
        (
            df['User-ID'].map(user_to_idx).values,
            df['ISBN'].map(isbn_to_idx).values
        )
    )
)

In [8]:
from sklearn.datasets import dump_svmlight_file
labels  = book_sparse_matrix.getcol(0).toarray().flatten()
dump_svmlight_file(book_sparse_matrix, labels, r'C:\Users\akile\Downloads\book_ratings.libsvm')

<h3> Project Step 2: Data Analysis </h3>

In [9]:
book_sparse_matrix

<105283x340556 sparse matrix of type '<class 'numpy.int64'>'
	with 1149780 stored elements in Compressed Sparse Row format>

In [10]:
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
import scipy.sparse as sp
from collections import defaultdict
from tqdm import tqdm

def find_similar_users_for_all(sparse_matrix, k=10, batch_size=1000):
    """
    Find K most similar users for every user in the sparse matrix.
    Uses batching for memory efficiency with large matrices.
    
    Parameters:
    -----------
    sparse_matrix : scipy.sparse matrix
        User-feature matrix in sparse format
    k : int
        Number of similar users to find (default: 10)
    batch_size : int
        Size of batches for processing (default: 1000)
        
    Returns:
    --------
    dict : Dictionary mapping each user_id to a tuple of (similar_user_indices, similarity_scores)
    """
    n_users = sparse_matrix.shape[0]
    similar_users_dict = {}
    
    # Process in batches to handle large matrices efficiently
    for start_idx in tqdm(range(0, n_users, batch_size), desc="Processing users"):
        end_idx = min(start_idx + batch_size, n_users)
        batch_users = sparse_matrix[start_idx:end_idx]
        
        # Calculate similarities for the batch
        similarities = cosine_similarity(batch_users, sparse_matrix)
        
        # For each user in the batch
        for i, user_similarities in enumerate(similarities):
            user_id = start_idx + i
            
            # Set self-similarity to negative infinity to exclude it
            user_similarities[user_id] = -np.inf
            
            # Get top K similar users
            similar_indices = np.argsort(user_similarities)[-k:][::-1]
            similarity_scores = user_similarities[similar_indices]
            if all(similarity_scores) == 0:
                continue
            # Store results
            similar_users_dict[user_id] = {
                'similar_users': similar_indices.tolist(),
                'similarity_scores': similarity_scores.tolist()
            }
    
    return similar_users_dict

def analyze_similarity_results(similar_users_dict):
    """
    Analyze the similarity results to provide useful statistics.
    
    Parameters:
    -----------
    similar_users_dict : dict
        Dictionary of similarity results from find_similar_users_for_all()
        
    Returns:
    --------
    dict : Dictionary containing various statistics about the similarities
    """
    all_similarities = []
    user_frequency = defaultdict(int)
    
    # Collect all similarity scores and count how often each user appears as similar
    for user_data in similar_users_dict.values():
        all_similarities.extend(user_data['similarity_scores'])
        for similar_user in user_data['similar_users']:
            user_frequency[similar_user] += 1
    
    # Calculate statistics
    stats = {
        'avg_similarity': np.mean(all_similarities),
        'median_similarity': np.median(all_similarities),
        'min_similarity': np.min(all_similarities),
        'max_similarity': np.max(all_similarities),
        'most_similar_users': sorted(user_frequency.items(), 
                                   key=lambda x: x[1], 
                                   reverse=True)[:10]
    }
    
    return stats

# Example usage:
def main():
    # Example of loading and processing LibSVM format
    # Assuming the sparse matrix is already loaded as 'sparse_matrix'
    
    # Find similar users
    similar_users = find_similar_users_for_all(book_sparse_matrix, k=10)
    
    # Analyze results
    stats = analyze_similarity_results(similar_users)
    
    # Print some example results
    print("\nSimilarity Statistics:")
    print(f"Average similarity score: {stats['avg_similarity']:.3f}")
    print(f"Median similarity score: {stats['median_similarity']:.3f}")
    print("\nMost frequently appearing similar users:")
    for user_id, frequency in stats['most_similar_users']:
        print(f"User {user_id}: appeared {frequency} times")
    return similar_users

In [11]:
similar_users = main()

Processing users: 100%|██████████| 106/106 [04:00<00:00,  2.27s/it]



Similarity Statistics:
Average similarity score: 0.538
Median similarity score: 0.482

Most frequently appearing similar users:
User 5063: appeared 278 times
User 19575: appeared 94 times
User 22728: appeared 83 times
User 34496: appeared 82 times
User 93550: appeared 82 times
User 96869: appeared 80 times
User 103851: appeared 80 times
User 27862: appeared 79 times
User 72229: appeared 77 times
User 47036: appeared 76 times


In [12]:
similar_users

{7: {'similar_users': [44523,
   52193,
   59069,
   47635,
   7388,
   58871,
   14203,
   57512,
   99295,
   78594],
  'similarity_scores': [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0]},
 10: {'similar_users': [38540,
   94885,
   79229,
   5882,
   69694,
   86317,
   46901,
   8854,
   90516,
   96374],
  'similarity_scores': [0.5,
   0.5,
   0.5,
   0.4444444444444444,
   0.4444444444444444,
   0.4444444444444444,
   0.4444444444444444,
   0.37370465934182984,
   0.3348247650912125,
   0.31980107453341566]},
 13: {'similar_users': [96979,
   7867,
   64334,
   12962,
   85203,
   69927,
   13824,
   52234,
   22602,
   35924],
  'similarity_scores': [1.0,
   1.0,
   1.0,
   1.0,
   1.0,
   1.0,
   1.0,
   1.0,
   0.8741572761215377,
   0.7525766947068778]},
 14: {'similar_users': [28901,
   73914,
   4351,
   76019,
   93509,
   73882,
   92585,
   78187,
   59486,
   74868],
  'similarity_scores': [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0]},
 16: {'similar_users': 

In [13]:
users = pd.read_csv(r"C:\Users\akile\Downloads\Book Dataset\Users.csv", delimiter=';')

C:\Users\akile\AppData\Local\Temp\ipykernel_16004\178755501.py:1: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  users = pd.read_csv(r"C:\Users\akile\Downloads\Book Dataset\Users.csv", delimiter=';')


In [14]:
users

User-ID  Age
0            1  NaN
1            2   18
2            3  NaN
3            4   17
4            5  NaN
...        ...  ...
278854  278854  NaN
278855  278855   50
278856  278856  NaN
278857  278857  NaN
278858  278858  NaN

[278859 rows x 2 columns]

In [15]:
print(len(similar_users))

40922


In [16]:
new_df = pd.DataFrame()
for user in similar_users:
    similar_user_nums = similar_users[user]["similar_users"]
    for sim_user in  similar_user_nums:
        sub_df = df[df["User-ID"] == idx_to_user[sim_user]]
        new_df = pd.concat([new_df, sub_df])
    new_df.to_csv(r"C:\Users\akile\Downloads\Book Dataset\similar_users_to_user{}.csv".format(user))
    break

In [17]:
import pickle
pickle.dump(similar_users, open(r"C:\Users\akile\Downloads\Book Dataset\similar_users.pkl", 'wb'))

In [18]:
import pickle
similar_users = pickle.load(open(r"C:\Users\akile\Downloads\Book Dataset\similar_users.pkl", 'rb'))

In [19]:
def get_similar_users_df(user, similar_users_dict, df):
    new_df = pd.DataFrame()
    user_to_idx = {user: idx for idx, user in enumerate(df['User-ID'].unique())}
    idx_to_user = {idx: user for user, idx in user_to_idx.items()}
    similar_user_nums = similar_users[user]["similar_users"]
    scores = similar_users[user]["similarity_scores"]
    for index, sim_user in enumerate(similar_user_nums):
        sub_df = df[df["User-ID"] == idx_to_user[sim_user]]
        sub_df["similarity_score"] = scores[index]
        sub_df["Total_sim_score"] = sum(scores)
        new_df = pd.concat([new_df, sub_df])
    return new_df

In [20]:
ratings_df = pd.read_csv(r"C:\Users\akile\Downloads\Book Dataset\ratings.csv", delimiter=';')
ratings_df.head()

User-ID        ISBN  Rating
0   276725  034545104X       0
1   276726  0155061224       5
2   276727  0446520802       0
3   276729  052165615X       3
4   276729  0521795028       6

In [21]:
def books_read_by_user(user, df):
    subd = df[df["User-ID"] == user]["ISBN"].values.tolist()
    return list(np.unique(subd))
    

In [22]:
import warnings
warnings.filterwarnings("ignore")
def get_weighted_ratings(books_read_by_user, similar_user_df):
    book_ids = np.unique(similar_user_df["ISBN"].values.tolist())
    final_books = [book for book in book_ids if book not in books_read_by_user]
    print(len(book_ids), len(final_books))
    new_rating_df = pd.DataFrame(columns=["ISBN", "Weighted_Rating"])
    
    for book_id in final_books:
        new_dict = {}
        sub_df = similar_user_df[similar_user_df["ISBN"] == book_id]
        numerator_term = 0
        denominator_term = 0
        for i, row in sub_df.iterrows():
            
            numerator_term += row["Rating"] * row["similarity_score"]
            denominator_term += row["similarity_score"]

        weighted_rating = numerator_term / denominator_term
        new_dict["ISBN"] = [book_id]
        new_dict["Weighted_Rating"] = [weighted_rating]
        new_rating_df = pd.concat([new_rating_df, pd.DataFrame(new_dict)])
        
    new_rating_df.sort_values(by="Weighted_Rating", ascending=False, inplace=True)
    return new_rating_df
        

In [23]:
from tqdm import tqdm
final_df = pd.DataFrame()
for user in tqdm(similar_users):
    user_books = books_read_by_user(user, ratings_df)
    similar_user_df = get_similar_users_df(user, similar_users, ratings_df)
    similar_weighted_df = get_weighted_ratings(user_books, similar_user_df)
    similar_weighted_df["User"] = pd.Series([user] * similar_weighted_df.shape[0])
    final_df = pd.concat([final_df, similar_weighted_df])

final_df.to_csv(r"C:\Users\akile\Downloads\Book Dataset\Similar_book_results_per_user.csv", index=False)
    
    

  0%|          | 3/40922 [00:00<1:06:00, 10.33it/s]

7 7
13 13
7 7
4 4
450 450


  0%|          | 5/40922 [00:00<2:08:36,  5.30it/s]

1050 1050


  0%|          | 8/40922 [00:02<3:07:55,  3.63it/s]

...

100%|█████████▉| 40920/40922 [10:45:09<00:01,  1.78it/s]

10 10


100%|█████████▉| 40921/40922 [10:45:09<00:00,  1.88it/s]

1619 1619


100%|██████████| 40922/40922 [10:45:11<00:00,  1.06it/s]


In [24]:
similar_users

{7: {'similar_users': [44523,
   52193,
   59069,
   47635,
   7388,
   58871,
   14203,
   57512,
   99295,
   78594],
  'similarity_scores': [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0]},
 10: {'similar_users': [38540,
   94885,
   79229,
   5882,
   69694,
   86317,
   46901,
   8854,
   90516,
   96374],
  'similarity_scores': [0.5,
   0.5,
   0.5,
   0.4444444444444444,
   0.4444444444444444,
   0.4444444444444444,
   0.4444444444444444,
   0.37370465934182984,
   0.3348247650912125,
   0.31980107453341566]},
 13: {'similar_users': [96979,
   7867,
   64334,
   12962,
   85203,
   69927,
   13824,
   52234,
   22602,
   35924],
  'similarity_scores': [1.0,
   1.0,
   1.0,
   1.0,
   1.0,
   1.0,
   1.0,
   1.0,
   0.8741572761215377,
   0.7525766947068778]},
 14: {'similar_users': [28901,
   73914,
   4351,
   76019,
   93509,
   73882,
   92585,
   78187,
   59486,
   74868],
  'similarity_scores': [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0]},
 16: {'similar_users': 

<h3> Results </h3>

In [3]:
import pandas as pd
results_df = pd.read_csv(r"C:\Users\akile\Downloads\Book Dataset\Similar_book_results_per_user.csv")
book_df = pd.read_csv(r"C:\Users\akile\Downloads\Book Dataset\Books.csv", delimiter=';')

In [4]:
book_df.head()

ISBN                                              Title  \
0  0195153448                                Classical Mythology   
1  0002005018                                       Clara Callan   
2  0060973129                               Decision in Normandy   
3  0374157065  Flu: The Story of the Great Influenza Pandemic...   
4  0393045218                             The Mummies of Urumchi   

                 Author  Year                Publisher  
0    Mark P. O. Morford  2002  Oxford University Press  
1  Richard Bruce Wright  2001    HarperFlamingo Canada  
2          Carlo D'Este  1991          HarperPerennial  
3      Gina Bari Kolata  1999     Farrar Straus Giroux  
4       E. J. W. Barber  1999   W. W. Norton & Company

In [33]:
book_df["ISBN"] = book_df["ISBN"].apply(lambda x: x.strip())

In [34]:
book_df

ISBN                                              Title  \
0       0195153448                                Classical Mythology   
1       0002005018                                       Clara Callan   
2       0060973129                               Decision in Normandy   
3       0374157065  Flu: The Story of the Great Influenza Pandemic...   
4       0393045218                             The Mummies of Urumchi   
...            ...                                                ...   
271374  0440400988                         There's a Bat in Bunk Five   
271375  0525447644                            From One to One Hundred   
271376  006008667X  Lily Dale : The True Story of the Town that Ta...   
271377  0192126040                        Republic (World's Classics)   
271378  0767409752  A Guided Tour of Rene Descartes' Meditations o...   

                      Author  Year  \
0         Mark P. O. Morford  2002   
1       Richard Bruce Wright  2001   
2               Carlo D'Este  1991   
3           Gina Bari Kolata  1999   
4            E. J. W. Barber  1999   
...                      ...   ...   
271374        Paula Danziger  1988   
271375            Teri Sloat  1991   
271376      Christine Wicker  2004   
271377                 Plato  1996   
271378   Christopher  Biffle  2000   

                                               Publisher  
0                                Oxford University Press  
1                                  HarperFlamingo Canada  
2                                        HarperPerennial  
3                                   Farrar Straus Giroux  
4                                 W. W. Norton & Company  
...                                                  ...  
271374                   Random House Childrens Pub (Mm)  
271375                                      Dutton Books  
271376                                HarperSanFrancisco  
271377                           Oxford University Press  
271378  McGraw-Hill Humanities/Social Sciences/Languages  

[271379 rows x 5 columns]

In [6]:
results_df.head()

ISBN  Weighted_Rating  User
0  038550120X              6.8     7
1   380820145              0.0     7
2   385495439              0.0     7
3   446678457              0.0     7
4   553380850              0.0     7

In [49]:
from tqdm import tqdm
final_df = pd.DataFrame()

for user_ind, (user, group) in enumerate(tqdm(results_df.groupby("User"))):
    for index, (row_index, row) in enumerate(group.iterrows()):
        if index < 5:
            print(user, index)
            row_dict = row.to_dict()
            isbn = row_dict["ISBN"]
            if len(isbn) < 10:
                zeros = "0" * (10 - len(isbn))
                isbn = zeros + isbn
            
            title = book_df[book_df["ISBN"] == isbn]["Title"]
            row_dict["Book_Title"] = title
            row_dict["ISBN"] = isbn
            final_df = pd.concat([final_df, pd.DataFrame(row_dict)], ignore_index=True)


  0%|          | 1/3636 [00:00<15:10,  3.99it/s]

7 0
7 1
7 2
7 3
7 4
10 0
10 1
10 2


  0%|          | 3/3636 [00:00<11:04,  5.46it/s]

10 3
10 4
13 0
13 1
13 2
13 3
13 4
14 0


  0%|          | 4/3636 [00:00<10:06,  5.99it/s]

...

9455 4
9460 0
9460 1
9460 2
9460 3
9460 4
9463 0
9463 1


100%|█████████▉| 3635/3636 [07:11<00:00,  7.53it/s]

9463 2
9463 3
9463 4
9464 0
9464 1
9464 2
9464 3
9464 4


100%|██████████| 3636/3636 [07:11<00:00,  8.43it/s]

9466 0
9466 1
9466 2
9466 3
9466 4


In [53]:
final_df.rename(columns={'ISBN': 'Book_ID', 'Weighted_Rating': 'Recommendation_Score', 'User': 'User_ID', 'Book_Title': 'Book_Title'}, inplace=True)
neworder = ['User_ID', 'Book_ID', 'Book_Title', 'Recommendation_Score']
final_df = final_df.reindex(columns=neworder)
final_df.to_csv(r"C:\Users\akile\Downloads\Book Dataset\Book_recommendation.csv", index=False)